In [1]:
import numpy as np
import xarray as xr
import matplotlib as mpl
#mpl.use('Agg') # Must be before importing matplotlib.pyplot or pylab!
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
from mpl_toolkits.axes_grid1.inset_locator import inset_axes

import pandas as pd
import os
import datetime
#import seaborn as sns
import timeit
import random
from dask.diagnostics import ProgressBar
from functools import partial
import dask

from scipy import ndimage

In [2]:
#%% plot parameters
mpl.rcParams['axes.linewidth'] = 2.0 #set the value globally
plt.rc('font', family='serif',size = 22)  # controls default text layout
plt.rc('axes', titlesize=22)     # fontsize of the axes title
plt.rc('axes', labelsize=22)    # fontsize of the x and y labels
plt.rc('xtick', labelsize=22)    # fontsize of the tick labels
plt.rc('ytick', labelsize=22)    # fontsize of the tick labels
plt.rc('legend', fontsize=22)    # legend fontsize
plt.rc('figure', titlesize=22)  # fontsize of the figure title

#sns.set()
#plt.minorticks_on()

plt.rc('text', usetex=False)


In [3]:
#setting progress bar visible
ProgressBar().register()
#making sure that xarray/dask splits large chunks while reading in data
dask.config.set({"array.slicing.split_large_chunks": True})

In [4]:
def _subset_process_time(ds,var,iop):
    
    #subset for the variable(s)
    ds = ds[var]
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if iop=='iop02': ds['time'] = pd.to_datetime('2019-08-22') + ds['time'].values
    #IOP03
    if iop=='iop03': ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values
    return(ds)

def _process_time(ds,iop):
    #round time to the nearest minute (30minute for PALM output)
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if iop=='iop02':ds['time'] = pd.to_datetime('2019-08-22') + ds['time'].values
    #IOP03
    if iop=='iop03':ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values    
    return(ds)

#function to concatenate all files for an ensemble member and if needed read in all ensemble members
def open_concat_member_files(ensemble_numbers,file,iop):
    data_list = []
    #loop through ensemble members
    if np.size(ensemble_numbers) > 1:
        for member_num in ensemble_numbers:    

            start_time = timeit.default_timer()
            if iop=='iop02': source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2/ensemble.member.'+str(member_num)
            #IOP03
            if iop=='iop03':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP03/OUTPUT/ensemble.member.'+str(member_num)         
            #file = 'DATA_3D_AV_NETCDF_N02slice' 

            #Make a folder list and read in all the files from those folders. 
            folder_list = os.listdir(source_folder) 
            folder_list.sort() 
            file_list = [] 
            for folder in folder_list: 
                file_list.append(source_folder + '/' +folder+'/'+file) 
            file_list.sort()
            print(folder_list)

            #combine all the data along the time dimenstion 
            #don't combine them sequentially, but infer the sequence from coordinate values 
            #do this in parallel 
            #pull in only those values with a time dimension 
            var = ['w','theta','q','u','v','wtheta','wq']
            partial_func = partial(_subset_process_time, var=var,iop=iop)
            ds = xr.open_mfdataset(file_list,preprocess=partial_func) 
            ds.close() 
            print('Member',str(member_num),'finished collecting data')    
            #subset for time and day and collect into another list
            #for day1
            data_list.append(ds)
            elapsed = timeit.default_timer() - start_time
            print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(data_list)
            
    else:
        member_num =ensemble_numbers

        #loop through ensemble members
        start_time = timeit.default_timer()
        #IOP02
        if iop=='iop02':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2/ensemble.member.'+str(member_num) 
        #IOP03
        if iop=='iop03':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP03/OUTPUT/ensemble.member.'+str(member_num) 
        
        #file = 'DATA_3D_AV_NETCDF_N03slice' 
        #file = 'DATA_1D_PR_NETCDF_N02slice' 

        #Make a folder list and read in all the files from those folders. 
        folder_list = os.listdir(source_folder) 
        folder_list.sort() 
        file_list = [] 
        for folder in folder_list: 
            file_list.append(source_folder + '/' +folder+'/'+file) 
        file_list.sort()
        print(folder_list)
        
        #combine all the data along the time dimenstion 
        partial_func = partial(_process_time,iop=iop)    
        ds = xr.open_mfdataset(file_list,preprocess=partial_func) 
        ds.close() 
        print('Member',str(member_num),'finished collecting data')    
        #subset for time and day and collect into another list
        #for day1
        #data_list.append(ds)
        elapsed = timeit.default_timer() - start_time
        print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(ds)




In [5]:
def _subset_process_time_hom(ds,var,iop):    
    #subset for the variable(s)
    ds = ds[var]
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if ds.time.dtype == '<m8[ns]': 
        if iop=='iop02': ds['time'] = pd.to_datetime('2019-08-22 22:00') + ds['time'].values
    #IOP03
    if ds.time.dtype == '<m8[ns]': 
        if iop=='iop03': ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values
    return(ds)

def _process_time_hom(ds,iop):
    #round time to the nearest minute (30minute for PALM output)
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if ds.time.dtype == '<m8[ns]':
        if iop=='iop02': ds['time'] = pd.to_datetime('2019-08-22 22:00') + ds['time'].values
        
    #IOP03
    if ds.time.dtype == '<m8[ns]': 
        if iop=='iop03': ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values    
    return(ds)


In [6]:
#function to concatenate all files for an ensemble member and if needed read in all ensemble members
def open_concat_member_files_hom(ensemble_numbers,file,iop):
    data_list = []
    #loop through ensemble members
    if np.size(ensemble_numbers) > 1:
        for member_num in ensemble_numbers:    

            start_time = timeit.default_timer()
            if iop=='iop02': source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.'+str(member_num) 
            if iop=='iop03': source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP3_parent_child1_hom/ensemble.member.'+str(member_num) 
            #file = 'DATA_3D_AV_NETCDF_N02slice' 

            #Make a folder list and read in all the files from those folders. 
            folder_list = os.listdir(source_folder) 
            folder_list.sort() 
            file_list = [] 
            for folder in folder_list: 
                file_list.append(source_folder + '/' +folder+'/'+file) 
            file_list.sort()
            print(folder_list)

            #combine all the data along the time dimenstion 
            #don't combine them sequentially, but infer the sequence from coordinate values 
            #do this in parallel 
            #pull in only those values with a time dimension 
            var = ['w','theta','q','u','v','wtheta','wq']
            partial_func = partial(_subset_process_time_hom, var=var,iop=iop)
            # open_mfdataset() called without chunks argument will return dask arrays with chunk sizes 
            # equal to the individual files. Re-chunking the dataset after creation with ds.chunk() will 
            # lead to an ineffective use of memory and is not recommended
            ds = xr.open_mfdataset(file_list,preprocess=partial_func,chunks={'time': 8}) 
            ds.close()
            #check if the time index has only unique values 
            u, c = np.unique(ds.time.values, return_counts=True)
            #if not, keep the second, latest value for the ds
            if np.sum(c > 1) > 0 : ds = ds.drop_duplicates(dim='time', keep='last')

            print('Member',str(member_num),'finished collecting data')
            
            #subset for time and day and collect into another list
            #for day1
            data_list.append(ds)
            elapsed = timeit.default_timer() - start_time
            print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(data_list)
            
    else:
        member_num =ensemble_numbers

        #loop through ensemble members
        start_time = timeit.default_timer()
        #IOP02
        if iop=='iop02': source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.'+str(member_num) 
        #IOP03
        if iop=='iop03':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP3_parent_child1_hom/ensemble.member.'+str(member_num) 
        
        #file = 'DATA_3D_AV_NETCDF_N03slice' 
        #file = 'DATA_1D_PR_NETCDF_N02slice' 

        #Make a folder list and read in all the files from those folders. 
        folder_list = os.listdir(source_folder) 
        folder_list.sort() 
        file_list = [] 
        for folder in folder_list: 
            file_list.append(source_folder + '/' +folder+'/'+file) 
        file_list.sort()
        print(folder_list)
        
        #combine all the data along the time dimenstion 
        partial_func = partial(_process_time_hom,iop=iop)    
        ds = xr.open_mfdataset(file_list,preprocess=partial_func) 
        ds.close() 
        #check if the time index has only unique values 
        u, c = np.unique(ds.time.values, return_counts=True)
        #if not, keep the second, latest value for the ds
        if np.sum(c > 1) > 0 : ds = ds.drop_duplicates(dim='time', keep='last')
        
        print('Member',str(member_num),'finished collecting data')    
        #subset for time and day and collect into another list
        #for day1
        #data_list.append(ds)
        elapsed = timeit.default_timer() - start_time
        print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(ds)

In [7]:
# create a dataset with all the ensembles, hom.
member_list = np.arange(1,9)

ensemble_ds_iop02_N02_list = open_concat_member_files_hom(member_list,'DATA_3D_AV_NETCDF_N02slice','iop02')
ensemble_ds_iop02_N02_hom = xr.concat(ensemble_ds_iop02_N02_list,dim='ensemble')

# # create a dataset with all the ensembles, hom.
# member_list = np.arange(1,9)

# ensemble_ds_iop02_P_list = open_concat_member_files_hom(member_list,'DATA_3D_AV_NETCDFslice','iop02')
# ensemble_ds_iop02_P_hom = xr.concat(ensemble_ds_iop02_P_list,dim='ensemble')


['00.ches_IOP2_parent_child1_hom1.9849', '01.ches_IOP2_parent_child1_hom1.29566', '02. ches_IOP2_parent_child1_hom1.9162', '03.ches_IOP2_parent_child1_hom1.7693']
Member 1 finished collecting data
Done with member 1  Time elapsed  1.4886570759117603 seconds
['01.ches_IOP2_parent_child1_hom.22675', '02.ches_IOP2_parent_child1_hom.4647']
Member 2 finished collecting data
Done with member 2  Time elapsed  0.5737544447183609 seconds
['00.ches_IOP2_parent_child1_hom3.8694', '01.ches_IOP2_parent_child1_hom3.9492', '02.ches_IOP2_parent_child1_hom3.14926', '03.ches_IOP2_parent_child1_hom3.22232']
Member 3 finished collecting data
Done with member 3  Time elapsed  1.4478611387312412 seconds
['00.ches_IOP2_parent_child1_hom4.31521', '01.ches_IOP2_parent_child1_hom4.20276', '02.ches_IOP2_parent_child1_hom4.808', '03.ches_IOP2_parent_child1_hom4.13218']
Member 4 finished collecting data
Done with member 4  Time elapsed  1.1361364908516407 seconds
['0.ches_IOP2_parent_child1_hom5.19920', '01.ches_I

In [8]:
# create a dataset with all the ensembles, hom.
member_list = np.arange(1,9)

ensemble_ds_iop03_N02_list = open_concat_member_files_hom(member_list,'DATA_3D_AV_NETCDF_N02slice','iop03')
ensemble_ds_iop03_N02_hom = xr.concat(ensemble_ds_iop03_N02_list,dim='ensemble')


['0.ches_IOP3_parent_child1_hom1.12767', '1.ches_IOP3_parent_child1_hom1.14954']
Member 1 finished collecting data
Done with member 1  Time elapsed  0.3236464560031891 seconds
['0.ches_IOP3_parent_child1_hom2.24067', '1.ches_IOP3_parent_child1_hom2.6737']
Member 2 finished collecting data
Done with member 2  Time elapsed  0.7153979688882828 seconds
['0.ches_IOP3_parent_child1_hom3.21914', '1.ches_IOP3_parent_child1_hom3.9923']
Member 3 finished collecting data
Done with member 3  Time elapsed  0.6895588487386703 seconds
['0.ches_IOP3_parent_child1_hom4.7100', '1.ches_IOP3_parent_child1_hom4.11437']
Member 4 finished collecting data
Done with member 4  Time elapsed  0.22920791059732437 seconds
['0.ches_IOP3_parent_child1_hom5.14681', '01.ches_IOP3_parent_child1_hom5.10912']
Member 5 finished collecting data
Done with member 5  Time elapsed  0.5030226558446884 seconds
['0.ches_IOP3_parent_child1_hom.14466', '01.ches_IOP3_parent_child1_hom.8882', '02.ches_IOP3_parent_child1_hom.27783', '0

In [9]:
IOP02_time_array = ['2019-08-23T09:00:00.000000000', '2019-08-23T09:30:00.000000000',
       '2019-08-23T10:00:00.000000000', '2019-08-23T10:30:00.000000000',
       '2019-08-23T11:00:00.000000000', '2019-08-23T11:30:00.000000000',
       '2019-08-23T12:00:00.000000000', '2019-08-23T12:30:00.000000000',
       '2019-08-23T13:00:00.000000000', '2019-08-23T13:30:00.000000000',
       '2019-08-23T14:00:00.000000000', '2019-08-23T14:30:00.000000000',
       '2019-08-23T15:00:00.000000000', '2019-08-23T15:30:00.000000000',
       '2019-08-23T16:00:00.000000000']

zi_iop02  =  [ 127.26811317,  186.28140789,  395.95448875,  490.1812074 ,
        767.58835375, 1194.99948318, 1242.73773669, 1400.52554689,
       1532.84613054, 1549.20057474, 1585.96478949, 1593.99945645,
       1598.73579416, 1618.02875473, 1621.44236578] 
zi_iop02_hom = [ 524.81832925, 1153.22989975, 1205.73771887, 1389.72816663,
       1504.96470929, 1528.45960793, 1561.48887948, 1572.03590109,
       1574.96876364, 1594.86374248, 1613.24770773]
u_star_iop02 = [0.23746523, 0.26933923, 0.34820446, 0.3888348 , 0.41974205,
       0.4338308 , 0.42021513, 0.41170758, 0.427308  , 0.4327292 ,
       0.41003117, 0.37822667, 0.37520644, 0.37473503, 0.35841644]
u_star_iop02_hom = [0.370922  , 0.37005759, 0.36280847, 0.37263662, 0.38041674,
       0.35737035, 0.33413935, 0.29965769, 0.29071767, 0.27624321,
       0.24543684]#1100 to 1600

w_star_iop02 = [0.65544301, 0.8218802 , 1.15222044, 1.33399153, 1.55739   ,
       1.80245719, 1.79051632, 1.88647701, 2.07238861, 2.06652333,
       2.0011327 , 1.89977991, 1.93889857, 1.9215422 , 1.82642433]
w_star_iop02_hom = [1.49996116, 1.95223882, 1.98763838, 2.12398263, 2.21043456,
       2.15475267, 2.08991902, 2.07123293, 2.04540851, 1.94049589,
       1.80304831]

theta_star_iop02 = [0.38440898, 0.41200343, 0.453697  , 0.4463509 , 0.42065033,
       0.38860902, 0.37801373, 0.45171738, 0.4704315 , 0.4525797 ,
       0.37480488, 0.40305007, 0.41563264, 0.36649814, 0.31710973]
theta_star_iop02_hom = [0.46344679, 0.46660581, 0.48116196, 0.4981287 , 0.50937209,
        0.49168755, 0.46601213, 0.50103008, 0.49510827, 0.43294575,
        0.40367009]

q_star_iop02 = [0.00021279, 0.00022559, 0.00024026, 0.00026083, 0.0002838 ,
       0.00027884, 0.0002789 , 0.00030576, 0.00030606, 0.00030307,
       0.00028612, 0.0003129 , 0.00031593, 0.0003026 , 0.00029867]
q_star_iop02_hom = [0.00031772, 0.00032474, 0.00033464, 0.00033697, 0.00033866,
       0.00034674, 0.00035412, 0.00039002, 0.0003958 , 0.00038738,
       0.00040821]

In [10]:
IOP03_time_array = ['2019-09-24T09:00:00.000000000', '2019-09-24T09:30:00.000000000',
       '2019-09-24T10:00:00.000000000', '2019-09-24T10:30:00.000000000',
       '2019-09-24T11:00:00.000000000', '2019-09-24T11:30:00.000000000',
       '2019-09-24T12:00:00.000000000', '2019-09-24T12:30:00.000000000',
       '2019-09-24T13:00:00.000000000', '2019-09-24T13:30:00.000000000',
       '2019-09-24T14:00:00.000000000', '2019-09-24T14:30:00.000000000']

zi_iop03 = [  89.55689018,  146.17518378,  222.75052796,  318.65739363,
        391.70175986,  465.53290265,  578.09552239,  665.90258855,
        747.14683894,  854.98633994,  961.446683  , 1046.67977723]

zi_iop03_hom = [ 85.71667632, 128.70966362, 186.86216084, 280.04332368,
       365.78988639, 493.88155937, 654.26742704, 754.06946759,
       830.85984406, 902.44667409, 950.16213856, 989.2927779 ]

u_star_array_iop03 = [0.10734038, 0.346752  , 0.42885262, 0.4882605 , 0.5238576 ,
       0.573982  , 0.60698235, 0.6250409 , 0.63989866, 0.6486785 ,
       0.651481  , 0.62593067]
u_star_array_iop03_hom = [ 0.09917983,  0.18773973,  0.31439638,  0.41304964,  0.45929348,
        0.49533993,  0.5244337 ,  0.5403172 , 44.93412   , 59.729065  ,
        0.5259894 ,  0.49205783]

theta_star_list_iop03 = [0.26582974, 0.22147681, 0.22207852, 0.20489082, 0.21669415,
       0.22336227, 0.2157141 , 0.20650086, 0.20044297, 0.18935573,
       0.17518993, 0.08177642]
theta_star_list_iop03_hom = [0.51723352, 0.39963672, 0.3056469 , 0.26371197, 0.26017615,
        0.25168263, 0.24436416, 0.23780183, 0.00277911, 0.00173605,
        0.15013228, 0.06724547]

w_star_list_iop03 = [0.28552411, 0.72898643, 0.80803615, 0.88109926, 0.94235606,
       1.07701186, 1.16389994, 1.21709966, 1.25004394, 1.28395841,
       1.31412257, 1.22432382]
w_star_list_iop03_hom = [0.5524251 , 0.71308628, 0.8732285 , 1.04171937, 1.17461117,
       1.31692814, 1.46028364, 1.52774717, 1.56301413, 1.52505127,
       1.43029462, 1.13401229]